## Описание проекта

Компания «Цифра» разрабатывает решения для эффективной работы промышленных предприятий. В нашем распоряжении данные с параметрами добычи и очистки.
Необходимо на основе предоставленных данных разработать модель, которая поможет оптимизировать производство, чтобы не запускать предприятие с убыточными характеристиками.

---

## Задача исследования

Подготовить прототип модели машинного обучения для «Цифры».
Модель должна предсказать коэффициент восстановления золота из золотосодержащей руды.

---

## Описание данных

### Технологический процесс

- _**Rougher feed**_ — исходное сырье
- _**Rougher additions (или reagent additions)**_ — флотационные реагенты: Xanthate, Sulphate, Depressant
- _**Xanthate**_ — ксантогенат (промотер, или активатор флотации);
- _**Sulphate**_ — сульфат (на данном производстве сульфид натрия);
- _**Depressant**_ — депрессант (силикат натрия).
- _**Rougher process**_ (англ. «грубый процесс») — флотация
- _**Rougher tails**_ — отвальные хвосты
- _**Float banks**_ — флотационная установка
- _**Cleaner process**_ — очистка
- _**Rougher Au**_ — черновой концентрат золота
- _**Final Au**_ — финальный концентрат золота

#### Параметры этапов

- _**air amount**_ — объём воздуха
- _**fluid levels**_ — уровень жидкости
- _**feed siz**_***e*** — размер гранул сырья
- _**feed rate**_ — скорость подачи

### Наименование признаков

Наименование признаков должно быть такое:

    [этап].[тип_параметра].[название_параметра]
    -------------------------------------------
    Пример: rougher.input.feed_ag

#### Возможные значения для блока [этап]:

- _**rougher**_ — флотация
- _**primary_cleaner**_ — первичная очистка
- _**secondary_cleaner**_ — вторичная очистка
- _**final**_ — финальные характеристики

#### Возможные значения для блока [тип_параметра]:

- _**input**_ — параметры сырья
- _**output**_ — параметры продукта
- _**state**_ — параметры, характеризующие текущее состояние этапа
- _**calculation**_ — расчётные характеристики

---
### Шаг 1. Изучим и подготовим данные

In [303]:
# импортируем библиотеки
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from sklearn.metrics import mean_absolute_error

In [258]:
# загрузим данные
gold_recovery_full = pd.read_csv('https://code.s3.yandex.net/datasets/gold_recovery_full_new.csv')
gold_recovery_train = pd.read_csv('https://code.s3.yandex.net/datasets/gold_recovery_train_new.csv')
gold_recovery_test = pd.read_csv('https://code.s3.yandex.net/datasets/gold_recovery_test_new.csv')
# дадим названия датасетам для удобства
gold_recovery_full.name = 'gold_recovery_full'
gold_recovery_train.name = 'gold_recovery_train'
gold_recovery_test.name = 'gold_recovery_test'
# также создадим список со всеми датасетами
all_data = [gold_recovery_full, gold_recovery_train, gold_recovery_test]

In [259]:
for data in all_data:
    display(f"{'='*10} Данные по датафрейму {data.name} {'='*10}")
    display(data.head())

'========== Данные по датафрейму gold_recovery_full =========='

date  final.output.concentrate_ag  \
0  2016-01-15 00:00:00                     6.055403   
1  2016-01-15 01:00:00                     6.029369   
2  2016-01-15 02:00:00                     6.055926   
3  2016-01-15 03:00:00                     6.047977   
4  2016-01-15 04:00:00                     6.148599   

   final.output.concentrate_pb  final.output.concentrate_sol  \
0                     9.889648                      5.507324   
1                     9.968944                      5.257781   
2                    10.213995                      5.383759   
3                     9.977019                      4.858634   
4                    10.142511                      4.939416   

   final.output.concentrate_au  final.output.recovery  final.output.tail_ag  \
0                    42.192020              70.541216             10.411962   
1                    42.701629              69.266198             10.462676   
2                    42.657501              68.116445             10.507046   
3                    42.689819              68.347543             10.422762   
4                    42.774141              66.927016             10.360302   

   final.output.tail_pb  final.output.tail_sol  final.output.tail_au  ...  \
0              0.895447              16.904297              2.143149  ...   
1              0.927452              16.634514              2.224930  ...   
2              0.953716              16.208849              2.257889  ...   
3              0.883763              16.532835              2.146849  ...   
4              0.792826              16.525686              2.055292  ...   

   secondary_cleaner.state.floatbank4_a_air  \
0                                 14.016835   
1                                 13.992281   
2                                 14.015015   
3                                 14.036510   
4                                 14.027298   

   secondary_cleaner.state.floatbank4_a_level  \
0                                 -502.488007   
1                                 -505.503262   
2                                 -502.520901   
3                                 -500.857308   
4                                 -499.838632   

   secondary_cleaner.state.floatbank4_b_air  \
0                                 12.099931   
1                                 11.950531   
2                                 11.912783   
3                                 11.999550   
4                                 11.953070   

   secondary_cleaner.state.floatbank4_b_level  \
0                                 -504.715942   
1                                 -501.331529   
2                                 -501.133383   
3                                 -501.193686   
4                                 -501.053894   

   secondary_cleaner.state.floatbank5_a_air  \
0                                  9.925633   
1                                 10.039245   
2                                 10.070913   
3                                  9.970366   
4                                  9.925709   

   secondary_cleaner.state.floatbank5_a_level  \
0                                 -498.310211   
1                                 -500.169983   
2                                 -500.129135   
3                                 -499.201640   
4                                 -501.686727   

   secondary_cleaner.state.floatbank5_b_air  \
0                                  8.079666   
1                                  7.984757   
2                                  8.013877   
3                                  7.977324   
4                                  7.894242   

   secondary_cleaner.state.floatbank5_b_level  \
0                                 -500.470978   
1                                 -500.582168   
2                                 -500.517572   
3                                 -500.255908   
4                                 -500.356035   

   secondary_cleaner.state.floatbank6_a_air  \
0    

'========== Данные по датафрейму gold_recovery_train =========='

date  final.output.concentrate_ag  \
0  2016-01-15 00:00:00                     6.055403   
1  2016-01-15 01:00:00                     6.029369   
2  2016-01-15 02:00:00                     6.055926   
3  2016-01-15 03:00:00                     6.047977   
4  2016-01-15 04:00:00                     6.148599   

   final.output.concentrate_pb  final.output.concentrate_sol  \
0                     9.889648                      5.507324   
1                     9.968944                      5.257781   
2                    10.213995                      5.383759   
3                     9.977019                      4.858634   
4                    10.142511                      4.939416   

   final.output.concentrate_au  final.output.recovery  final.output.tail_ag  \
0                    42.192020              70.541216             10.411962   
1                    42.701629              69.266198             10.462676   
2                    42.657501              68.116445             10.507046   
3                    42.689819              68.347543             10.422762   
4                    42.774141              66.927016             10.360302   

   final.output.tail_pb  final.output.tail_sol  final.output.tail_au  ...  \
0              0.895447              16.904297              2.143149  ...   
1              0.927452              16.634514              2.224930  ...   
2              0.953716              16.208849              2.257889  ...   
3              0.883763              16.532835              2.146849  ...   
4              0.792826              16.525686              2.055292  ...   

   secondary_cleaner.state.floatbank4_a_air  \
0                                 14.016835   
1                                 13.992281   
2                                 14.015015   
3                                 14.036510   
4                                 14.027298   

   secondary_cleaner.state.floatbank4_a_level  \
0                                 -502.488007   
1                                 -505.503262   
2                                 -502.520901   
3                                 -500.857308   
4                                 -499.838632   

   secondary_cleaner.state.floatbank4_b_air  \
0                                 12.099931   
1                                 11.950531   
2                                 11.912783   
3                                 11.999550   
4                                 11.953070   

   secondary_cleaner.state.floatbank4_b_level  \
0                                 -504.715942   
1                                 -501.331529   
2                                 -501.133383   
3                                 -501.193686   
4                                 -501.053894   

   secondary_cleaner.state.floatbank5_a_air  \
0                                  9.925633   
1                                 10.039245   
2                                 10.070913   
3                                  9.970366   
4                                  9.925709   

   secondary_cleaner.state.floatbank5_a_level  \
0                                 -498.310211   
1                                 -500.169983   
2                                 -500.129135   
3                                 -499.201640   
4                                 -501.686727   

   secondary_cleaner.state.floatbank5_b_air  \
0                                  8.079666   
1                                  7.984757   
2                                  8.013877   
3                                  7.977324   
4                                  7.894242   

   secondary_cleaner.state.floatbank5_b_level  \
0                                 -500.470978   
1                                 -500.582168   
2                                 -500.517572   
3                                 -500.255908   
4                                 -500.356035   

   secondary_cleaner.state.floatbank6_a_air  \
0    

'========== Данные по датафрейму gold_recovery_test =========='

date  primary_cleaner.input.sulfate  \
0  2016-09-01 00:59:59                     210.800909   
1  2016-09-01 01:59:59                     215.392455   
2  2016-09-01 02:59:59                     215.259946   
3  2016-09-01 03:59:59                     215.336236   
4  2016-09-01 04:59:59                     199.099327   

   primary_cleaner.input.depressant  primary_cleaner.input.feed_size  \
0                         14.993118                         8.080000   
1                         14.987471                         8.080000   
2                         12.884934                         7.786667   
3                         12.006805                         7.640000   
4                         10.682530                         7.530000   

   primary_cleaner.input.xanthate  primary_cleaner.state.floatbank8_a_air  \
0                        1.005021                             1398.981301   
1                        0.990469                             1398.777912   
2                        0.996043                             1398.493666   
3                        0.863514                             1399.618111   
4                        0.805575                             1401.268123   

   primary_cleaner.state.floatbank8_a_level  \
0                               -500.225577   
1                               -500.057435   
2                               -500.868360   
3                               -498.863574   
4                               -500.808305   

   primary_cleaner.state.floatbank8_b_air  \
0                             1399.144926   
1                             1398.055362   
2                             1398.860436   
3                             1397.440120   
4                             1398.128818   

   primary_cleaner.state.floatbank8_b_level  \
0                               -499.919735   
1                               -499.778182   
2                               -499.764529   
3                               -499.211024   
4                               -499.504543   

   primary_cleaner.state.floatbank8_c_air  ...  \
0                             1400.102998  ...   
1                             1396.151033  ...   
2                             1398.075709  ...   
3                             1400.129303  ...   
4                             1402.172226  ...   

   secondary_cleaner.state.floatbank4_a_air  \
0                                 12.023554   
1                                 12.058140   
2                                 11.962366   
3                                 12.033091   
4                                 12.025367   

   secondary_cleaner.state.floatbank4_a_level  \
0                                 -497.795834   
1                                 -498.695773   
2                                 -498.767484   
3                                 -498.350935   
4                                 -500.786497   

   secondary_cleaner.state.floatbank4_b_air  \
0                                  8.016656   
1                                  8.130979   
2                                  8.096893   
3                                  8.074946   
4                                  8.054678   

   secondary_cleaner.state.floatbank4_b_level  \
0                                 -501.289139   
1                                 -499.634209   
2                                 -500.827423   
3                                 -499.474407   
4                                 -500.397500   

   secondary_cleaner.state.floatbank5_a_air  \
0                                  7.946562   
1                                  7.958270   
2                                  8.071056   
3                                  7.897085   
4                                  8.107890   

   secondary_cleaner.state.floatbank5_a_level  \
0                                 -432.317850   
1                                 -525.839648   
2                                 -500.801673   
3     

In [260]:
for data in all_data:
    display(f"{'='*10} Данные по датафрейму {data.name} {'='*10}")
    data.info()

'========== Данные по датафрейму gold_recovery_full =========='

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 19439 entries, 0 to 19438
Data columns (total 87 columns):
 #   Column                                              Non-Null Count  Dtype  
---  ------                                              --------------  -----  
 0   date                                                19439 non-null  object 
 1   final.output.concentrate_ag                         19438 non-null  float64
 2   final.output.concentrate_pb                         19438 non-null  float64
 3   final.output.concentrate_sol                        19228 non-null  float64
 4   final.output.concentrate_au                         19439 non-null  float64
 5   final.output.recovery                               19439 non-null  float64
 6   final.output.tail_ag                                19438 non-null  float64
 7   final.output.tail_pb                                19338 non-null  float64
 8   final.output.tail_sol                               19433 non-null  float64


'========== Данные по датафрейму gold_recovery_train =========='

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 14149 entries, 0 to 14148
Data columns (total 87 columns):
 #   Column                                              Non-Null Count  Dtype  
---  ------                                              --------------  -----  
 0   date                                                14149 non-null  object 
 1   final.output.concentrate_ag                         14148 non-null  float64
 2   final.output.concentrate_pb                         14148 non-null  float64
 3   final.output.concentrate_sol                        13938 non-null  float64
 4   final.output.concentrate_au                         14149 non-null  float64
 5   final.output.recovery                               14149 non-null  float64
 6   final.output.tail_ag                                14149 non-null  float64
 7   final.output.tail_pb                                14049 non-null  float64
 8   final.output.tail_sol                               14144 non-null  float64


'========== Данные по датафрейму gold_recovery_test =========='

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5290 entries, 0 to 5289
Data columns (total 53 columns):
 #   Column                                      Non-Null Count  Dtype  
---  ------                                      --------------  -----  
 0   date                                        5290 non-null   object 
 1   primary_cleaner.input.sulfate               5286 non-null   float64
 2   primary_cleaner.input.depressant            5285 non-null   float64
 3   primary_cleaner.input.feed_size             5290 non-null   float64
 4   primary_cleaner.input.xanthate              5286 non-null   float64
 5   primary_cleaner.state.floatbank8_a_air      5290 non-null   float64
 6   primary_cleaner.state.floatbank8_a_level    5290 non-null   float64
 7   primary_cleaner.state.floatbank8_b_air      5290 non-null   float64
 8   primary_cleaner.state.floatbank8_b_level    5290 non-null   float64
 9   primary_cleaner.state.floatbank8_c_air      5290 non-null   float64
 10  primary_clea

Во всех датасетах имеется колонка с датой в строковом формате.
В датасете gold_recovery_train имеем всего 53 признака, что на 34 меньше, чем в остальных.
Также наблюдаются пропуски в некоторых колонках.

Проверим правильность рассчета эффективности обогащения. Для этого вычислим ее вручную на обучающей выборке и найдем значение MAE между ручными рассчетами и соответствущим признаком в данных по формуле:
![](https://pictures.s3.yandex.net/resources/Recovery_1576238822.jpg)

где:
 - C — доля золота в концентрате после флотации/очистки;
 - F — доля золота в сырье/концентрате до флотации/очистки;
 - T — доля золота в отвальных хвостах после флотации/очистки.

In [261]:
def calculate_output_recovery(row: pd.DataFrame) -> pd.Series:
    C, F, T = row
    # print(C,F,T)
    return (C*(F-T)) / (F*(C-T)) * 100

In [262]:
# рассчитаем вручную
handly_calc_recovery = gold_recovery_train[['rougher.output.concentrate_au', 'rougher.input.feed_au', 'rougher.output.tail_au']].apply(calculate_output_recovery, axis=1)
# рассчитаем МАЕ
mean_absolute_error(gold_recovery_train['rougher.output.recovery'], handly_calc_recovery)

9.73512347450521e-15

Очень маленькая величина ошибки говорит нам о том, что эффективность обогащения в датасете рассчитана верно.

Посмотрим какие признаки недоступны в тестовой выборке.

In [263]:
set(gold_recovery_train.columns) - set(gold_recovery_test.columns)

{'final.output.concentrate_ag',
 'final.output.concentrate_au',
 'final.output.concentrate_pb',
 'final.output.concentrate_sol',
 'final.output.recovery',
 'final.output.tail_ag',
 'final.output.tail_au',
 'final.output.tail_pb',
 'final.output.tail_sol',
 'primary_cleaner.output.concentrate_ag',
 'primary_cleaner.output.concentrate_au',
 'primary_cleaner.output.concentrate_pb',
 'primary_cleaner.output.concentrate_sol',
 'primary_cleaner.output.tail_ag',
 'primary_cleaner.output.tail_au',
 'primary_cleaner.output.tail_pb',
 'primary_cleaner.output.tail_sol',
 'rougher.calculation.au_pb_ratio',
 'rougher.calculation.floatbank10_sulfate_to_au_feed',
 'rougher.calculation.floatbank11_sulfate_to_au_feed',
 'rougher.calculation.sulfate_to_au_concentrate',
 'rougher.output.concentrate_ag',
 'rougher.output.concentrate_au',
 'rougher.output.concentrate_pb',
 'rougher.output.concentrate_sol',
 'rougher.output.recovery',
 'rougher.output.tail_ag',
 'rougher.output.tail_au',
 'rougher.output.ta

В тестовой выборке недоступны 2 типа параметров:
 - _output_
 - _calculation_

Вероятно данные типа _output_ получаем после проведения определенного этапа обработки, т.о. эти данные не попали в тестовую выборку, т.к. их использовать нельзя.
Данные типа _calculation_ получаем в результате вычислений на основе уже предоставленных данных, поэтому они также не попали в тестовую выборку.

Удалим данные колонки из обучающей выборки.

In [264]:
cols_to_delete_from_train = set(gold_recovery_train.columns) - set(gold_recovery_test.columns)
gold_recovery_train.drop(cols_to_delete_from_train, axis=1, inplace=True)
gold_recovery_train.shape

(14149, 53)

Теперь преобразуем дату в datetime формат.

In [265]:
for data in all_data:
    data['date'] = pd.to_datetime(data['date'], format='%Y-%m-%d %H:%M:%S')
    display(f"Данные по колонке date датасета {data.name}")
    data['date'].info()

'Данные по колонке date датасета gold_recovery_full'

<class 'pandas.core.series.Series'>
RangeIndex: 19439 entries, 0 to 19438
Series name: date
Non-Null Count  Dtype         
--------------  -----         
19439 non-null  datetime64[ns]
dtypes: datetime64[ns](1)
memory usage: 152.0 KB


'Данные по колонке date датасета gold_recovery_train'

<class 'pandas.core.series.Series'>
RangeIndex: 14149 entries, 0 to 14148
Series name: date
Non-Null Count  Dtype         
--------------  -----         
14149 non-null  datetime64[ns]
dtypes: datetime64[ns](1)
memory usage: 110.7 KB


'Данные по колонке date датасета gold_recovery_test'

<class 'pandas.core.series.Series'>
RangeIndex: 5290 entries, 0 to 5289
Series name: date
Non-Null Count  Dtype         
--------------  -----         
5290 non-null   datetime64[ns]
dtypes: datetime64[ns](1)
memory usage: 41.5 KB


Проверим, есть ли в данных пропуски

In [266]:
def get_missing_values(data: pd.DataFrame) -> None:
    """
    Выводит данные о пропусках в колонках по датафрейму.
    Не изменяет данные внутри датафрейма.

    :param data: pd.DataFrame
    :return: None
    """
    # получаем имена колонок датафрейма
    columns = data.columns.to_list()
    data_len = len(data)
    # объявляем счетчик
    counter = -1
    print('='*60)
    # если есть пропуски в данных - выводим информацию о пропусках по колонкам
    if sum(data.isnull().sum()) > 0:
        print(f'Количество записей в датафрейме {data.name}: {data_len} \n')
        print(f'В датафрейме {data.name} имеются следующие пропуски:')
        for i in data.isnull().sum():
            counter += 1
            if i > 0:
                print(f'  - в колонке {columns[counter]}: {i} пропусков, это {i/data_len:0.2%} об общего объема данных')
    else:
        print(f'Отлично, в датафрейме {data.name} отсутствуют пропуски.')

# посмотрим на пропуски в данных
for data in all_data:
    display(f'Проверка пропусков в датасете {data.name}')
    get_missing_values(data)

'Проверка пропусков в датасете gold_recovery_full'

Количество записей в датафрейме gold_recovery_full: 19439 

В датафрейме gold_recovery_full имеются следующие пропуски:
  - в колонке final.output.concentrate_ag: 1 пропусков, это 0.01% об общего объема данных
  - в колонке final.output.concentrate_pb: 1 пропусков, это 0.01% об общего объема данных
  - в колонке final.output.concentrate_sol: 211 пропусков, это 1.09% об общего объема данных
  - в колонке final.output.tail_ag: 1 пропусков, это 0.01% об общего объема данных
  - в колонке final.output.tail_pb: 101 пропусков, это 0.52% об общего объема данных
  - в колонке final.output.tail_sol: 6 пропусков, это 0.03% об общего объема данных
  - в колонке primary_cleaner.input.sulfate: 24 пропусков, это 0.12% об общего объема данных
  - в колонке primary_cleaner.input.depressant: 37 пропусков, это 0.19% об общего объема данных
  - в колонке primary_cleaner.input.xanthate: 104 пропусков, это 0.54% об общего объема данных
  - в колонке primary_cleaner.output.concentrate_pb: 116 пропусков, это

'Проверка пропусков в датасете gold_recovery_train'

Количество записей в датафрейме gold_recovery_train: 14149 

В датафрейме gold_recovery_train имеются следующие пропуски:
  - в колонке primary_cleaner.input.sulfate: 20 пропусков, это 0.14% об общего объема данных
  - в колонке primary_cleaner.input.depressant: 32 пропусков, это 0.23% об общего объема данных
  - в колонке primary_cleaner.input.xanthate: 100 пропусков, это 0.71% об общего объема данных
  - в колонке primary_cleaner.state.floatbank8_a_air: 4 пропусков, это 0.03% об общего объема данных
  - в колонке primary_cleaner.state.floatbank8_a_level: 1 пропусков, это 0.01% об общего объема данных
  - в колонке primary_cleaner.state.floatbank8_b_air: 4 пропусков, это 0.03% об общего объема данных
  - в колонке primary_cleaner.state.floatbank8_b_level: 1 пропусков, это 0.01% об общего объема данных
  - в колонке primary_cleaner.state.floatbank8_c_air: 2 пропусков, это 0.01% об общего объема данных
  - в колонке primary_cleaner.state.floatbank8_c_level: 1 пропусков, это 0.01% об общ

'Проверка пропусков в датасете gold_recovery_test'

Количество записей в датафрейме gold_recovery_test: 5290 

В датафрейме gold_recovery_test имеются следующие пропуски:
  - в колонке primary_cleaner.input.sulfate: 4 пропусков, это 0.08% об общего объема данных
  - в колонке primary_cleaner.input.depressant: 5 пропусков, это 0.09% об общего объема данных
  - в колонке primary_cleaner.input.xanthate: 4 пропусков, это 0.08% об общего объема данных
  - в колонке rougher.input.feed_rate: 3 пропусков, это 0.06% об общего объема данных
  - в колонке rougher.input.feed_size: 1 пропусков, это 0.02% об общего объема данных
  - в колонке rougher.input.feed_sol: 21 пропусков, это 0.40% об общего объема данных
  - в колонке rougher.input.floatbank10_sulfate: 5 пропусков, это 0.09% об общего объема данных
  - в колонке rougher.input.floatbank11_sulfate: 8 пропусков, это 0.15% об общего объема данных
  - в колонке rougher.input.floatbank11_xanthate: 25 пропусков, это 0.47% об общего объема данных
  - в колонке secondary_cleaner.state.floatbank2_a_ai

В колонке secondary_cleaner.output.tail_sol наблюдается большое количество пропусков.
В остальных колонках пропусков не более 3.5%, а зачастую и единичные пропуски, можем эти данные удалить.

Для начала заполним пропуски в колонке secondary_cleaner.output.tail_sol датасета full.
Для этого посмотрим на среднее и медиану по данной колонке, увидим, есть ли выбросы в данных по разнице этих значений и примем решение как будем заполнять пропуски.

In [268]:
gold_recovery_full['secondary_cleaner.output.tail_sol'].agg(['mean', 'median'])

mean      7.167247
median    7.685827
Name: secondary_cleaner.output.tail_sol, dtype: float64

Среднее и медиана незначительно отличаются, в данных практически отсутствуют выбросы, а значит заполним пропуски средним значением столбца.

In [269]:
gold_recovery_full['secondary_cleaner.output.tail_sol'].fillna(gold_recovery_full['secondary_cleaner.output.tail_sol'].mean(), inplace=True)

Избавимся от пропусков.

In [270]:
for data in all_data:
    # удалим пропуски
    data.dropna(inplace=True)
    # проверим что пропуски удалены корректно
    get_missing_values(data)

Отлично, в датафрейме gold_recovery_full отсутствуют пропуски.
Отлично, в датафрейме gold_recovery_train отсутствуют пропуски.
Отлично, в датафрейме gold_recovery_test отсутствуют пропуски.


Проверим данные на наличие явных дублей.

In [273]:
for data in all_data:
    print(f"Количество дублей в атасете {data.name}: {data.duplicated().sum()}")

Количество дублей в атасете gold_recovery_full: 0
Количество дублей в атасете gold_recovery_train: 0
Количество дублей в атасете gold_recovery_test: 0


Отлично, дубликаты отсутствуют.

---

## Шаг 2. Анализ данных.

Посмотрим, как меняется концентрация металлов на различных этапах очистки.

In [316]:
for idx, metall in enumerate(['concentrate_au', 'concentrate_ag', 'concentrate_pb']):
    titles = ['золота', 'серебра', 'свинца']
    fig = go.Figure()
    columns_to_plot = []
    for col in gold_recovery_full.columns:
        if metall in col:
            name = col.split('.')[0]
            fig.add_trace(
                go.Histogram(
                    dict(x=gold_recovery_full[col]),
                    name=name,
                    opacity=.6)
            )
    fig.update_layout(
        title=f'Распределение концентрации {titles[idx]} в руде на различных этапах очистки',
        legend_orientation="h",
        legend=dict(x=.62, y=-.2),
        margin=dict(l=20, r=10, t=80, b=10),
        hovermode="x",
        barmode="overlay",
        bargap=0.15
    )
    fig.update_traces(hovertemplate=f"Концентрация {titles[idx]}: {'%{x}'}<br>"
                                    "Количество фракций: %{y}")
    fig.update_xaxes(
        title=f'Концентрация {titles[idx]}'
    )
    fig.update_yaxes(
        title='Количество фракций'
    )
    fig.show()


Промежуточные выводы.

1. Золото
 - концентрация золота в руде увеличивается от этапа флотации до финальной очистки
 - довольно четкие распределения концентрации руды на каждом этапе очистки может говорить нам о хорошо налаженном производстве и процессов очистки руды для добычи золота
 - на каждом этапе очистки видны длинные левые хвосты распределений, которые говорят нам о том, что в ходе очистки руды, остаются довольно мелкие фракции золота
 - после каждого этапа очистки отвальных хвостов становится все меньше

2. Серебро
 - концентрация серебра уменьшается от этапа флотации до финальной очистки
 - после каждого этапа очистки отвальных хвостов становится все меньше

3. Свинец
 - концентрация свинца увеличивается после этапа флотации, на этапе основной и финально очистки концентрация остается в среднем на одном уровне
 - на этапе основной очистки наблюдаем довольно тяжелые хвосты у распределения, что может сказать нам либо об особенностях формирования свинца в руде (часто встречаются мелкие фракции свинца), или о сложностях очистки руды с высокой концентрацией свинца или о том, что этот этап очистки нуждается в доработке
 - после каждого этапа очистки отвальных хвостов становится все меньше

In [292]:
gold_recovery_full['final.output.concentrate_ag']

0        6.055403
1        6.029369
2        6.055926
3        6.047977
4        6.148599
           ...   
19434    3.224920
19435    3.195978
19436    3.109998
19437    3.367241
19438    3.598375
Name: final.output.concentrate_ag, Length: 17390, dtype: float64